In [18]:
#このセルでは、ひとまずSuperconのデータを使ってcrabnetを適当に試してみる

In [6]:
import pandas as pd
pd.set_option('display.max_rows', 1000)
pd.set_option('display.max_columns', 1000)

In [7]:
#まずsuperconのデータを適当に分析する

SC_data = pd.read_csv("/workspaces/mat2vec_codespace/main_code/20240322_Supercon_data_allstr_handedited.csv", encoding='utf-8')
missing_values = SC_data.isnull().sum()
print(missing_values)

/workspaces/mat2vec_codespace/.venv/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3553: DtypeWarning: Columns (0,6,8,10,12,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,58,59,61,62,63,64,65,66,67,68,69,70,71,72,73,76,77,78,79,80,81,82,84,86,87,88,89,90,91,92,94,95,96,97,98,99,100,101,103,104,105,106,107,108,109,110,112,113,114,115,117,119,120,121,122,124,125,126,127,128,129,130,131,132,133,134,136,137,139,140,141,142,143,144,145,146,147,148,149,150,151,154,155,156,157,158,159,160,161,162,163,164,165,166,167,168,169,170,171,172,174,175,176,177,179,180,181,182,184,190) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


data number                                                         0
reference number                                                    0
comment                                                         18280
common formula of materials                                      1517
chemical formula                                                    0
element name of materials                                           0
composition of MA1                                                  0
element name of materials.1                                       416
composition of MA2                                                428
element name of materials.2                                      6667
composition of MA3                                               6684
element name of materials.3                                     17488
composition of MA4                                              17520
element name of materials.4                                     27632
composition of MA5  

In [8]:
#crab_input_data = SC_data.loc[:, ["chemical formula", "Tc (of this sample) recommended", "oxygen", "common formula of oxygen", "measured value of Oxygen content", "title of reference"]].rename(columns={"chemical formula": "formula", "Tc (of this sample) recommended": "Tc"})
crab_input_data = SC_data.rename(columns={"chemical formula": "formula", "Tc (of this sample) recommended": "Tc"})

In [9]:
crab_input_data = crab_input_data[crab_input_data["Tc"].notna()]
crab_input_data = crab_input_data.iloc[1:, :]

In [8]:
#現状判明していることとして、酸素数関連のデータに問題がいろいろとあるので
#酸素がある物質については酸素の具体的な量が乗っているデータは組成式にそれを組み込んで
#使ってないデータは消す方針でいったん動く
#まず酸化物とそうでないものを分ける

In [10]:
NonOxide_SC_data = crab_input_data[crab_input_data["oxygen"].isna()].drop(columns=["oxygen", "common formula of oxygen", "measured value of Oxygen content"])
Oxide_SC_data = crab_input_data[crab_input_data["oxygen"].notna()]

In [11]:
#measured valueがある場合
measured_value_of_Oxygen_index = Oxide_SC_data.loc[:, "measured value of Oxygen content"].notna()
Oxide_SC_data.loc[measured_value_of_Oxygen_index, "value of oxygen"] = Oxide_SC_data.loc[measured_value_of_Oxygen_index, "measured value of Oxygen content"]


/workspaces/mat2vec_codespace/.venv/lib/python3.7/site-packages/pandas/core/indexing.py:1681: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = empty_value
/workspaces/mat2vec_codespace/.venv/lib/python3.7/site-packages/pandas/core/indexing.py:1773: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(ilocs[0], value, pi)


In [12]:
#measured valueがないがcommon formulaに数字がある場合
common_value_of_Oxygen_index = Oxide_SC_data.loc[:, "measured value of Oxygen content"].isna() & Oxide_SC_data.loc[:, "common formula of oxygen"].str.isdigit()
Oxide_SC_data.loc[common_value_of_Oxygen_index, "value of oxygen"] = Oxide_SC_data.loc[common_value_of_Oxygen_index, "common formula of oxygen"]

In [13]:
final_Oxide_SC_data = Oxide_SC_data.drop(columns=["oxygen", "common formula of oxygen", "measured value of Oxygen content"])
final_Oxide_SC_data = final_Oxide_SC_data[final_Oxide_SC_data["value of oxygen"].notna()]

In [14]:
new_SC_data = pd.concat([final_Oxide_SC_data, NonOxide_SC_data], axis = 0).reset_index(drop = True)

In [15]:
new_SC_data["Tc"] = new_SC_data["Tc"].astype(float)

In [11]:
pd.set_option('display.max_colwidth', 500)

In [16]:
#new_SC_data = new_SC_data.sort_values("Tc", ascending = False)

In [17]:
check_words = ["pressure", "gpa", "mbar"]

In [18]:
high_pressure_data = new_SC_data["title of reference"].astype(str).apply(lambda x: any(word.lower() in x.lower() for word in check_words))
not_high_pressure_data = ~high_pressure_data

In [19]:
final_SC_data = new_SC_data[not_high_pressure_data].iloc[5:, :].drop(columns = ["title of reference"])

In [20]:
final_SC_data.to_csv("/workspaces/mat2vec_codespace/main_code/final_SC_X_data_ver2.csv", index = False)

In [21]:
display(final_SC_data.head(10))

data number reference number comment common formula of materials  \
5          106       APL0500543     NaN                (La,Sr)2CuO4   
6          108       JJP0260337     NaN           (La,Sr)2(Cu,Ti)O4   
7          109       JJP0260337     NaN            (La,Sr)2(Cu,V)O4   
8          110       JJP0260337     NaN           (La,Sr)2(Cu,Cr)O4   
9          111       JJP0260337     NaN           (La,Sr)2(Cu,Mn)O4   
10         112       JJP0260337     NaN           (La,Sr)2(Cu,Fe)O4   
11         113       JJP0260337     NaN           (La,Sr)2(Cu,Co)O4   
12         114       JJP0260337     NaN           (La,Sr)2(Cu,Ni)O4   
13         115       JJP0260337     NaN           (La,Sr)2(Cu,Zn)O4   
14         116       JJP0260337     NaN             (La,Pr,Sr)2CuO4   

                     formula element name of materials composition of MA1  \
5          Sr0.15La1.85Cu1O4                        Sr               0.15   
6   Sr0.2La1.8Cu0.95Ti0.05O4                        Sr                0.2   
7    Sr0.2La1.8Cu0.99V0.01O4                        Sr                0.2   
8   Sr0.2La1.8Cu0.99Cr0.01O4                        Sr                0.2   
9   Sr0.2La1.8Cu0.98Mn0.02O4                        Sr                0.2   
10  Sr0.2La1.8Cu0.95Fe0.05O4                        Sr                0.2   
11  Sr0.2La1.8Cu0.95Co0.05O4                        Sr                0.2   
12  Sr0.2La1.8Cu0.95Ni0.05O4                        Sr                0.2   
13  Sr0.2La1.8Cu0.99Zn0.01O4                        Sr                0.2   
14      Pr0.1La1.7Sr0.2Cu1O4                        Pr                0.1   

   element name of materials.1 composition of MA2 element name of materials.2  \
5                           La               1.85                          Cu   
6                           La                1.8                          Cu   
7                           La                1.8                          Cu   
8                           La                1.8                          Cu   
9                           La                1.8                          Cu   
10                          La                1.8                          Cu   
11                          La                1.8                          Cu   
12                          La                1.8                          Cu   
13                          La                1.8                          Cu   
14                          La                1.7                          Sr   

   composition of MA3 element name of materials.3 composition of MA4  \
5                   1                         NaN                NaN   
6                0.95                          Ti               0.05   
7                0.99                           V               0.01   
8                0.99                          Cr               0.01   
9                0.98                          Mn               0.02   
10               0.95                          Fe               0.05   
11               0.95                          Co               0.05   
12               0.95                          Ni               0.05   
13               0.99                          Zn               0.01   
14                0.2                          Cu                  1   

   element name of materials.4 composition of MA5 element name of materials.5  \
5                          NaN                NaN                         NaN   
6                          NaN                NaN                         NaN   
7                          NaN                NaN                         NaN   
8                          NaN                NaN                         NaN   
9                          NaN                NaN                         NaN   
10                         NaN                NaN                         NaN   
11                         NaN                NaN                         NaN   
12                         NaN          

In [4]:
SC_data = pd.read_csv("/workspaces/mat2vec_codespace/main_code/final_SC_X_data_ver2.csv", encoding='utf-8')
missing_values = SC_data.isnull().sum()
print(missing_values)

data number                                                         0
reference number                                                    0
comment                                                          9864
common formula of materials                                       966
formula                                                             0
element name of materials                                           0
composition of MA1                                                  0
element name of materials.1                                       250
composition of MA2                                                253
element name of materials.2                                      4441
composition of MA3                                               4449
element name of materials.3                                     10959
composition of MA4                                              10968
element name of materials.4                                     16183
composition of MA5  

/workspaces/mat2vec_codespace/.venv/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3553: DtypeWarning: Columns (15,17,19,21,23,27,36,38,41,44,49,55,56,62,63,67,81,86,91,109,114,131,133,137,139,140,145,164,171,173,177,178,179,186) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [22]:
display(SC_data.loc[SC_data.loc[:, "composition of MA2"].isna(), :])

data number reference number  \
591           617       JPS0572261   
3239         3268       SSC0810253   
3240         3269       SSC0810253   
3241         3270       SSC0810253   
3751         3781       SSC0710419   
3766         3796       SSC0651529   
3930         3960       SSC0670119   
5061         5097       PHC1970042   
5087         5123       SSC0850073   
5379         5416       PHC2340024   
5441         5478       PHC2430252   
5490         5527       PHC2410211   
5519         5556       PLA1960263   
5548         5585       PHC2420012   
10105       10344       PR05003221   
10897       12070       L094097002   
10898       12071       L094097002   
10899       12072       L094097002   
14820       40000        PR0950333   
14821       40001        PR0950333   
14822       40002        PR0950333   
14823       40003        PR0950333   
14824       40004        PR0950333   
14825       40005        PR0950333   
14826       40006        PR0950333   
14827       40007        PR0950333   
14828       40008        PR1040549   
14829       40009        PR0860235   
14830       40010        PR0860235   
14831       40011        PR0860235   
14832       40012        PR0840691   
14837       40017       PLA0240340   
14838       40018       PLA0240340   
14839       40019        PR1550364   
14840       40020        PR1550364   
14841       40021        PR1550364   
14842       40022        PR0104572   
14845       40026        PR0024442   
14846       40027        PR0024442   
14847       40028        PR0024442   
14848       40029        PR0024442   
14993       40178       PLA0150303   
14994       40179        PR1660457   
14995       40180        PR1640565   
15002       40187        PR1410407   
15003       40188        PR1311105   
15004       40189        PR1121888   
15005       40190        PR1121522   
15139       40324       ZPS1950215   
15140       40325       ZPS1950215   
15143       40328       L096057001   
15309       40495       P073094522   
15310       40496       PRL0190892   
15449       40740       SCI2922462   
15558       40855       PR140A1620   
15576       40873       P072060512   
15773       42076       PHC4510082   
15774       42077       J075083703   
15806       42109       PHY0550663   
15807       42110       PHY0550663   
15808       42111       PHY0550663   
15809       42112       PHY0550663   
15821       42125       PHC4530012   
15904       50023       PHB2630296   
16016       50143        PR0337820   
16017       50144        PR0337820   
16089       90095       PRL0391161   
16090       90096       PRB0250194   
16091       90097       PRB0250194   
16092       90098       PRL0231375   
16093       90099       PRL0231375   
16098       90104       PRL0420469   
16099       90105       JPS0593843   
16100       90106       PRL0794262   
16101       90107       PRL0794262   
16102       90108        PR1120031   
16103       90109        PR1120031   
16104       90110        PR1120031   
16105       90111        PR1120031   
16106       90112        PR1120031   
16107       90113        PR1120031   
16108       90114       PRL0350104   
16109       90115       PRL0441623   
16110       90116       PR05016274   
16112       90118        PR0465523   
16113       90119        PR0337820   
16114       90120        PR0337820   
16115       90121       FTT0142527   
16157       90163             1555   
16158       90164             1555   
16202       90209        PR1220459   
16203       90210        PR1590353   
16355       90362        PR1201964   
16357       90364        PR1291025   
16422      100064              762   
16635      100277             1830   
16821      100463              710   
16822      100464             1702   
16823      100465             1702   
16824      100466             1702   
16825      100467             1702   
16826      100468             1233   
17254      100901             1607   
17277      100924             1609   
17290      10093